In [1]:
import altair as alt
import json
import numpy as np
import pandas as pd

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
df = pd.read_csv('../data/tirol_obituaries_deduped.csv', delimiter = ',')

In [3]:
df['date'] = pd.to_datetime(df['date'], format='%d.%m.%Y')
df.head()

date  year  week               municipaly        district        hash
0 2020-04-22  2020    17                    Fließ         Landeck   425347311
1 2020-04-22  2020    17       Oberndorf in Tirol       Kitzbühel -1610007678
2 2020-04-21  2020    17  St. Sigmund im Sellrain  Innsbruck-Land  1983856866
3 2020-04-21  2020    17                  Jenbach          Schwaz   916421891
4 2020-04-21  2020    17         Eben am Achensee          Schwaz  1698728696

In [4]:
#http://www.statistik.at/wcm/idc/idcplg?IdcService=GET_NATIVE_FILE&RevisionSelectionMethod=LatestReleased&dDocName=122943
statistik_austria = pd.DataFrame({
    'week': [14,13,12,11,10,9,8,7,6,5,4,3,2,1],
    'death_count': [153,152,136,130,128,137,123,117,119,132,133,138,136,123]
})
statistik_austria.head()

week  death_count
0    14          153
1    13          152
2    12          136
3    11          130
4    10          128

In [5]:
base = alt.Chart(df, width=400, height=200)

x_domain=(1,52)

week_point = base.transform_filter(
    'datum.year==2020 & datum.week<17'
).mark_circle(color='red', opacity=0, size=150).encode(
    alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
    alt.Y('count()', title=''),
    tooltip=['year', 'week', 'count()']
)

week_historic_area = base.transform_filter(
    'datum.year!=2020 && datum.year!=2016'
).mark_area(color='lightgray', opacity=0.5).transform_joinaggregate(
    week_count='count()',
    groupby=['week','year']
).encode(
    alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
    alt.Y('max(week_count):Q', title=''),
    alt.Y2('min(week_count):Q', title='')
)

week_historic_mean = base.transform_filter(
    'datum.year!=2020 && datum.year!=2016'
).mark_line(color='gray', opacity=0.25).transform_joinaggregate(
    week_count='count()',
    groupby=['week','year']
).encode(
    alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
    alt.Y('mean(week_count):Q', title='')
)

week_current_line = base.transform_filter(
    'datum.year==2020 & datum.week<17'
).mark_line(clip=True,).transform_joinaggregate(
    week_count='count()',
    groupby=['week','year']
).encode(
    alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
    alt.Y('week_count:Q', title='', axis=alt.Axis(domainOpacity=0,ticks=False)),
    tooltip=['year:Q', 'week:Q', 'week_count:Q']
)

week_statistik_austria_line = alt.Chart(statistik_austria).transform_filter(
    'datum.week<=12'
).mark_line(clip=True,color='orange').encode(
    alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
    alt.Y('death_count:Q', title='', axis=alt.Axis(domainOpacity=0,ticks=False)),
    tooltip=['week:Q', 'death_count:Q']
)
week_statistik_austria_line_estimate = alt.Chart(statistik_austria).transform_filter(
    'datum.week>=12'
).mark_line(clip=True,color='orange',opacity=0.5,strokeDash=[3,2]).encode(
    alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
    alt.Y('death_count:Q', title='', axis=alt.Axis(domainOpacity=0,ticks=False)),
    tooltip=['week:Q', 'death_count:Q']
)

chart_3_legendDomain = [
    'Statistik Austria 2020 inkl. Schätzung',
    'Todesanzeigen 2020',
    'Todesanzeigen 2017-2019 min/max',
    'Todesanzeigen 2017-2019 mean'
]
chart_3_legendColors = ['orange', '#1f77b4', 'lightgray', 'gray']
chart_3_legendData = pd.DataFrame({
    'label': chart_3_legendDomain
})

legend3 = alt.Chart(chart_3_legendData).mark_square(size=150).encode(
    y=alt.Y(
        'label:N',
        axis=alt.Axis(domain=False, ticks=False, orient='right'),
        title=None
    ),
    color=alt.Color(
        'label',
        scale=alt.Scale(domain=chart_3_legendDomain,range=chart_3_legendColors),
        legend=None
    )
)

vega_week = ((
    week_historic_area +
    week_historic_mean +
    week_statistik_austria_line +
    week_statistik_austria_line_estimate +
    week_current_line +
    week_point
) | legend3).properties(
    title={
      "text": ["Todesanzeigen Tirol pro Woche im Jahresverlauf"],
    }
).configure_axis(
    grid=True,
    gridColor="#eee",
    domainColor="#ddd",
    tickColor="#ddd",
    labelColor="gray",
    labelBound=True,
).configure_view(
    strokeWidth=0
).configure_title(
    fontSize=14,
    fontWeight='bold',
    anchor='start',
    color='gray'
)

vega_week

alt.HConcatChart(...)

In [6]:
def district_chart(district='Kufstein'):
    d_df = df[df['district']==district]

    d_base = alt.Chart(d_df).properties(
        width=220,
        height=125
    )

    x_domain=(1,52)

    d_week_point = d_base.transform_filter(
        'datum.year==2020 & datum.week<17'
    ).mark_circle(color='gray', opacity=0, size=150).transform_joinaggregate(
        count='count()',
        groupby=['week','year']
    ).encode(
        alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
        alt.Y('count:Q', title=''),
        tooltip=['year:Q', 'week:Q', 'count:Q']
    )

    d_week_historic_area = d_base.transform_filter(
        'datum.year!=2020 && datum.year!=2016'
    ).mark_area(color='lightgray', opacity=0.5).transform_joinaggregate(
        week_count='count()',
        groupby=['week','year']
    ).encode(
        alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
        alt.Y('max(week_count):Q', title=''),
        alt.Y2('min(week_count):Q', title='')
    )

    d_week_historic_mean = d_base.transform_filter(
        'datum.year!=2020 && datum.year!=2016'
    ).mark_line(color='gray', opacity=0.25).transform_joinaggregate(
        week_count='count()',
        groupby=['week','year']
    ).encode(
        alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
        alt.Y('mean(week_count):Q', title='')
    )

    d_week_current_line = d_base.transform_filter(
        'datum.year==2020 & datum.week<17'
    ).mark_line(clip=True,).transform_joinaggregate(
        week_count='count()',
        groupby=['week','year']
    ).encode(
        alt.X('week:Q', scale=alt.Scale(domain=x_domain,zero=False,nice=False), title='', axis=alt.Axis(grid=False)),
        alt.Y('week_count:Q', title='', axis=alt.Axis(domainOpacity=0,ticks=False))
    )

    return (
        d_week_historic_area +
        d_week_historic_mean +
        d_week_current_line +
        d_week_point
    ).properties(
        title={
          "text": [district],
        }
    )

d_chart_3_legendDomain = [
    'Todesanzeigen 2020',
    'Todesanzeigen 2017-2019 min/max',
    'Todesanzeigen 2017-2019 mean'
]
d_chart_3_legendColors = ['#1f77b4', 'lightgray', 'gray']
d_chart_3_legendData = pd.DataFrame({
    'label': d_chart_3_legendDomain
})


d_legend3 = alt.Chart(d_chart_3_legendData).mark_square(size=150).encode(
    y=alt.Y(
        'label:N',
        axis=alt.Axis(domain=False, ticks=False, orient='right'),
        title=None
    ),
    color=alt.Color(
        'label',
        scale=alt.Scale(domain=d_chart_3_legendDomain,range=d_chart_3_legendColors),
        legend=None
    )
)

vega_week_district = (
    (
         district_chart('Imst') | district_chart('Innsbruck-Stadt') | district_chart('Innsbruck-Land')
    ) & (
        district_chart('Kitzbühel') | district_chart('Kufstein') | district_chart('Landeck')
    ) & (
        district_chart('Lienz') | district_chart('Reutte') | district_chart('Schwaz')
    ) | d_legend3
).configure_axis(
        grid=True,
        gridColor="#eee",
        domainColor="#ddd",
        tickColor="#ddd",
        labelColor="gray",
        labelBound=True,
    ).configure_view(
        strokeWidth=0
    ).configure_title(
        fontSize=14,
        fontWeight='normal',
        anchor='start',
        color='gray'
    )

vega_week_district

alt.HConcatChart(...)

In [7]:
# save chart_1 as formatted JSON
with open("../charts/vega_week.json", "w") as jsonFile:
    json.dump(json.loads(vega_week.to_json()), jsonFile, indent=4, sort_keys=True)

In [8]:
# save chart_1 as formatted JSON
with open("../charts/vega_week_district.json", "w") as jsonFile:
    json.dump(json.loads(vega_week_district.to_json()), jsonFile, indent=4, sort_keys=True)